In [1]:
!pip install ftfy
import csv
import os
from collections import defaultdict
import pandas as pd
from nltk.corpus import stopwords
from textblob import TextBlob, Word
from gensim.scripts.glove2word2vec import glove2word2vec
from nltk.stem import PorterStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
from gensim.models import KeyedVectors # load the Stanford GloVe model
import ftfy
import string
from nltk.tokenize import word_tokenize
import pickle

#nltk.download()

In [2]:
#reading csv
train = pd.read_csv('data/theonion.csv', encoding='ISO-8859-1',low_memory=False)
#train

In [3]:
train = train[train.notnull()]
#train

In [4]:
train = train.dropna(how='any') 
#train

In [10]:
heads = train['headline']
#heads

In [11]:
descs = train['body']
#descs

In [12]:
title_list = []
for i in heads:
    title = ftfy.fix_text(i)
    title_list.append(title)  

In [13]:
title_list

['inclement weather prevents liar from getting to work',
 "mother comes pretty close to using word 'streaming' correctly",
 "richard branson's global-warming donation nearly as much as cost of failed balloon trips",
 'shadow government getting too large to meet in marriott conference room b',
 'ford develops new suv that runs purely on gasoline',
 'area boy enters jumping-and-touching-tops-of-doorways phase',
 'guard in video game under strict orders to repeatedly pace same stretch of hallway',
 'secret service agent not so secret about being david alan grier fan',
 'leading probability researchers confounded by three coworkers wearing same shirt color on same day',
 "new york introduces shoe-sharing program for city's pedestrians",
 'expansive obama state of the union speech to touch on patent law, entomology, the films of robert altman',
 'naacp demands less minority representation on upn',
 'god getting strong urge to bring back dinosaurs',
 'handshake comes in at unusually high ang

In [14]:
content_list = []
for i in descs:
    descs = ftfy.fix_text(i)
    content_list.append(descs)

In [15]:
content_list[0]

'PROVIDENCE, RI—In spite of his best efforts to brave the ongoing winter storm and freezing temperatures, the inclement weather currently affecting the Northeast has left Providence-area liar Tim Carlson unable to commute to his office, the habitual deceiver reported to his colleagues today. "They haven\'t been able to plow my street yet and the snow drifts have to be two feet high in some places, so I don\'t really think there\'s any way for me to make it in," said an email sent from the man who spent 45 minutes attempting to dislodge his car from a snowbank and who routinely fabricates stories. "On top of that, the buses don\'t seem to be running in my area, or else I definitely would have been in by now. This is really a mess. I\'m so sorry, everyone. Wish I could be there." Carlson also confirmed that the weather had left his apartment\'s electricity somewhat spotty, preventing the unrepentant phony from doing any work from home.'

In [16]:

title_list = [''.join(c for c in s if c not in string.punctuation) for s in title_list]


In [17]:
content_list = [''.join(c for c in s if c not in string.punctuation) for s in content_list]


In [18]:
tokenized_title = [word_tokenize(i) for i in title_list]

In [19]:
tokenized_title

[['inclement', 'weather', 'prevents', 'liar', 'from', 'getting', 'to', 'work'],
 ['mother',
  'comes',
  'pretty',
  'close',
  'to',
  'using',
  'word',
  'streaming',
  'correctly'],
 ['richard',
  'bransons',
  'globalwarming',
  'donation',
  'nearly',
  'as',
  'much',
  'as',
  'cost',
  'of',
  'failed',
  'balloon',
  'trips'],
 ['shadow',
  'government',
  'getting',
  'too',
  'large',
  'to',
  'meet',
  'in',
  'marriott',
  'conference',
  'room',
  'b'],
 ['ford',
  'develops',
  'new',
  'suv',
  'that',
  'runs',
  'purely',
  'on',
  'gasoline'],
 ['area', 'boy', 'enters', 'jumpingandtouchingtopsofdoorways', 'phase'],
 ['guard',
  'in',
  'video',
  'game',
  'under',
  'strict',
  'orders',
  'to',
  'repeatedly',
  'pace',
  'same',
  'stretch',
  'of',
  'hallway'],
 ['secret',
  'service',
  'agent',
  'not',
  'so',
  'secret',
  'about',
  'being',
  'david',
  'alan',
  'grier',
  'fan'],
 ['leading',
  'probability',
  'researchers',
  'confounded',
  'by',
  

In [20]:
tokenized_content = [word_tokenize(i) for i in content_list]

In [21]:
tokenized_content[0]

['PROVIDENCE',
 'RI—In',
 'spite',
 'of',
 'his',
 'best',
 'efforts',
 'to',
 'brave',
 'the',
 'ongoing',
 'winter',
 'storm',
 'and',
 'freezing',
 'temperatures',
 'the',
 'inclement',
 'weather',
 'currently',
 'affecting',
 'the',
 'Northeast',
 'has',
 'left',
 'Providencearea',
 'liar',
 'Tim',
 'Carlson',
 'unable',
 'to',
 'commute',
 'to',
 'his',
 'office',
 'the',
 'habitual',
 'deceiver',
 'reported',
 'to',
 'his',
 'colleagues',
 'today',
 'They',
 'havent',
 'been',
 'able',
 'to',
 'plow',
 'my',
 'street',
 'yet',
 'and',
 'the',
 'snow',
 'drifts',
 'have',
 'to',
 'be',
 'two',
 'feet',
 'high',
 'in',
 'some',
 'places',
 'so',
 'I',
 'dont',
 'really',
 'think',
 'theres',
 'any',
 'way',
 'for',
 'me',
 'to',
 'make',
 'it',
 'in',
 'said',
 'an',
 'email',
 'sent',
 'from',
 'the',
 'man',
 'who',
 'spent',
 '45',
 'minutes',
 'attempting',
 'to',
 'dislodge',
 'his',
 'car',
 'from',
 'a',
 'snowbank',
 'and',
 'who',
 'routinely',
 'fabricates',
 'stories',
 

In [22]:
stop = stopwords.words('english')

In [23]:
filtered_title = [word for word in tokenized_title if word not in stop]


In [24]:
filtered_title

[['inclement', 'weather', 'prevents', 'liar', 'from', 'getting', 'to', 'work'],
 ['mother',
  'comes',
  'pretty',
  'close',
  'to',
  'using',
  'word',
  'streaming',
  'correctly'],
 ['richard',
  'bransons',
  'globalwarming',
  'donation',
  'nearly',
  'as',
  'much',
  'as',
  'cost',
  'of',
  'failed',
  'balloon',
  'trips'],
 ['shadow',
  'government',
  'getting',
  'too',
  'large',
  'to',
  'meet',
  'in',
  'marriott',
  'conference',
  'room',
  'b'],
 ['ford',
  'develops',
  'new',
  'suv',
  'that',
  'runs',
  'purely',
  'on',
  'gasoline'],
 ['area', 'boy', 'enters', 'jumpingandtouchingtopsofdoorways', 'phase'],
 ['guard',
  'in',
  'video',
  'game',
  'under',
  'strict',
  'orders',
  'to',
  'repeatedly',
  'pace',
  'same',
  'stretch',
  'of',
  'hallway'],
 ['secret',
  'service',
  'agent',
  'not',
  'so',
  'secret',
  'about',
  'being',
  'david',
  'alan',
  'grier',
  'fan'],
 ['leading',
  'probability',
  'researchers',
  'confounded',
  'by',
  

In [25]:
filtered_content = [word for word in tokenized_content if word not in stop]


In [26]:
filtered_content

[['PROVIDENCE',
  'RI—In',
  'spite',
  'of',
  'his',
  'best',
  'efforts',
  'to',
  'brave',
  'the',
  'ongoing',
  'winter',
  'storm',
  'and',
  'freezing',
  'temperatures',
  'the',
  'inclement',
  'weather',
  'currently',
  'affecting',
  'the',
  'Northeast',
  'has',
  'left',
  'Providencearea',
  'liar',
  'Tim',
  'Carlson',
  'unable',
  'to',
  'commute',
  'to',
  'his',
  'office',
  'the',
  'habitual',
  'deceiver',
  'reported',
  'to',
  'his',
  'colleagues',
  'today',
  'They',
  'havent',
  'been',
  'able',
  'to',
  'plow',
  'my',
  'street',
  'yet',
  'and',
  'the',
  'snow',
  'drifts',
  'have',
  'to',
  'be',
  'two',
  'feet',
  'high',
  'in',
  'some',
  'places',
  'so',
  'I',
  'dont',
  'really',
  'think',
  'theres',
  'any',
  'way',
  'for',
  'me',
  'to',
  'make',
  'it',
  'in',
  'said',
  'an',
  'email',
  'sent',
  'from',
  'the',
  'man',
  'who',
  'spent',
  '45',
  'minutes',
  'attempting',
  'to',
  'dislodge',
  'his',


In [27]:
title_new = [' '.join(c for c in s if c not in string.punctuation) for s in filtered_title]

In [28]:
content_new = [' '.join(c for c in s if c not in string.punctuation) for s in filtered_content]

In [29]:
title_new

['inclement weather prevents liar from getting to work',
 'mother comes pretty close to using word streaming correctly',
 'richard bransons globalwarming donation nearly as much as cost of failed balloon trips',
 'shadow government getting too large to meet in marriott conference room b',
 'ford develops new suv that runs purely on gasoline',
 'area boy enters jumpingandtouchingtopsofdoorways phase',
 'guard in video game under strict orders to repeatedly pace same stretch of hallway',
 'secret service agent not so secret about being david alan grier fan',
 'leading probability researchers confounded by three coworkers wearing same shirt color on same day',
 'new york introduces shoesharing program for citys pedestrians',
 'expansive obama state of the union speech to touch on patent law entomology the films of robert altman',
 'naacp demands less minority representation on upn',
 'god getting strong urge to bring back dinosaurs',
 'handshake comes in at unusually high angle velocity',

In [30]:
content_new

['PROVIDENCE RI—In spite of his best efforts to brave the ongoing winter storm and freezing temperatures the inclement weather currently affecting the Northeast has left Providencearea liar Tim Carlson unable to commute to his office the habitual deceiver reported to his colleagues today They havent been able to plow my street yet and the snow drifts have to be two feet high in some places so I dont really think theres any way for me to make it in said an email sent from the man who spent 45 minutes attempting to dislodge his car from a snowbank and who routinely fabricates stories On top of that the buses dont seem to be running in my area or else I definitely would have been in by now This is really a mess Im so sorry everyone Wish I could be there Carlson also confirmed that the weather had left his apartments electricity somewhat spotty preventing the unrepentant phony from doing any work from home',
 'PATERSON NJ—Family sources told reporters Tuesday that local mother Karen Burkha

In [31]:
final_list = pd.DataFrame(
    {'heads': title_new,
     'descs': content_new,
    })

In [36]:
final_list.to_csv('data/theonion_processed.csv')

In [37]:
final_list.to_pickle('tokenized_data.pickle')

In [38]:
df2 = pd.read_pickle('tokenized_data.pickle')
train_data = df2.iloc[:100000]
train_data.to_pickle('train_data.pkl')
validation_data = df2.iloc[100001:130000]
validation_data.to_pickle('validation_data.pkl')
test_data = df2.iloc[130001:142568]
test_data.to_pickle('test_data.pkl')